In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import itertools as it
from pandas import to_datetime

from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error

from prophet import Prophet

C:\Users\wujin\anaconda3\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
df = pd.read_csv('primary_school_clean.csv', index_col='Year', parse_dates=True)
df.head()

School Phase  Vacancy  Applied  Taken  \
Year                                                                      
2009-01-01      Admiralty Primary School     1      300      168    168   
2009-01-01  Ahmad Ibrahim Primary School     1      180       57     57   
2009-01-01                Ai Tong School     1      330      144    144   
2009-01-01   Anchor Green Primary School     1      240       50     50   
2009-01-01       Anderson Primary School     1      240      106    106   

           Balloting  Application Rate  
Year                                    
2009-01-01       NaN          0.560000  
2009-01-01       NaN          0.316667  
2009-01-01       NaN          0.436364  
2009-01-01       NaN          0.208333  
2009-01-01       NaN          0.441667

In [3]:
df.reset_index(inplace=True)

In [4]:
# Drop Phase 2C(S) and Phase 3 as those phases are not competitive.
df.drop(df[(df['Phase'] == '3') | (df['Phase'] == '2C(S)')].index, inplace=True)

In [5]:
df

Year                        School Phase  Vacancy  Applied  Taken  \
0     2009-01-01      Admiralty Primary School     1      300      168    168   
1     2009-01-01  Ahmad Ibrahim Primary School     1      180       57     57   
2     2009-01-01                Ai Tong School     1      330      144    144   
3     2009-01-01   Anchor Green Primary School     1      240       50     50   
4     2009-01-01       Anderson Primary School     1      240      106    106   
...          ...                           ...   ...      ...      ...    ...   
10039 2022-01-01        Zhangde Primary School    2C       93       92     92   
10040 2022-01-01       Zhenghua Primary School    2C       90       68     68   
10041 2022-01-01       Zhonghua Primary School    2C      115        7      7   
10042 2022-01-01         Valour Primary School    2C       96      120     96   
10043 2022-01-01     Northshore Primary School    2C      175       75     75   

      Balloting  Application Rate  
0           NaN          0.560000  
1           NaN          0.316667  
2           NaN          0.436364  
3           NaN          0.208333  
4           NaN          0.441667  
...         ...               ...  
10039       NaN          0.989247  
10040       NaN          0.755556  
10041       NaN          0.060870  
10042      SC<1          1.250000  
10043       NaN          0.428571  

[10044 rows x 8 columns]

In [6]:
# Get indices of Phase 1
df[(df['Year'] == '2022-01-01') & (df['Phase'] == '1')]

Year                        School Phase  Vacancy  Applied  Taken  \
2330 2022-01-01      Admiralty Primary School     1      150      107    107   
2331 2022-01-01  Ahmad Ibrahim Primary School     1      130       56     56   
2332 2022-01-01                Ai Tong School     1      240      130    130   
2333 2022-01-01      Alexandra Primary School     1      140       75     75   
2334 2022-01-01   Anchor Green Primary School     1      180       75     75   
...         ...                           ...   ...      ...      ...    ...   
2506 2022-01-01        Zhangde Primary School     1      120       75     75   
2507 2022-01-01       Zhenghua Primary School     1      180       91     91   
2508 2022-01-01       Zhonghua Primary School     1       90       28     28   
2509 2022-01-01         Valour Primary School     1      220      105    105   
2510 2022-01-01     Northshore Primary School     1      180       33     33   

     Balloting  Application Rate  
2330       NaN          0.713333  
2331       NaN          0.430769  
2332       NaN          0.541667  
2333       NaN          0.535714  
2334       NaN          0.416667  
...        ...               ...  
2506       NaN          0.625000  
2507       NaN          0.505556  
2508       NaN          0.311111  
2509       NaN          0.477273  
2510       NaN          0.183333  

[181 rows x 8 columns]

In [7]:
# Get indices of Phase 2A
df[(df['Year'] == '2022-01-01') & (df['Phase'] == '2A')]

Year                        School Phase  Vacancy  Applied  Taken  \
4841 2022-01-01      Admiralty Primary School    2A       44       37     37   
4842 2022-01-01  Ahmad Ibrahim Primary School    2A       74        5      5   
4843 2022-01-01                Ai Tong School    2A      110      146    110   
4844 2022-01-01      Alexandra Primary School    2A       65        9      9   
4845 2022-01-01   Anchor Green Primary School    2A      105       46     46   
...         ...                           ...   ...      ...      ...    ...   
5017 2022-01-01        Zhangde Primary School    2A       45       11     11   
5018 2022-01-01       Zhenghua Primary School    2A       89       59     59   
5019 2022-01-01       Zhonghua Primary School    2A       62        6      6   
5020 2022-01-01         Valour Primary School    2A      115       77     77   
5021 2022-01-01     Northshore Primary School    2A      147       31     31   

     Balloting  Application Rate  
4841       NaN          0.840909  
4842       NaN          0.067568  
4843       NaN          1.327273  
4844       NaN          0.138462  
4845       NaN          0.438095  
...        ...               ...  
5017       NaN          0.244444  
5018       NaN          0.662921  
5019       NaN          0.096774  
5020       NaN          0.669565  
5021       NaN          0.210884  

[181 rows x 8 columns]

In [8]:
# Get indices of Phase 2B
df[(df['Year'] == '2022-01-01') & (df['Phase'] == '2B')]

Year                        School Phase  Vacancy  Applied  Taken  \
7352 2022-01-01      Admiralty Primary School    2B       22       49     22   
7353 2022-01-01  Ahmad Ibrahim Primary School    2B       43        0      0   
7354 2022-01-01                Ai Tong School    2B       20       48     20   
7355 2022-01-01      Alexandra Primary School    2B       39        4      4   
7356 2022-01-01   Anchor Green Primary School    2B       40        0      0   
...         ...                           ...   ...      ...      ...    ...   
7528 2022-01-01        Zhangde Primary School    2B       31        1      1   
7529 2022-01-01       Zhenghua Primary School    2B       30        0      0   
7530 2022-01-01       Zhonghua Primary School    2B       39        1      1   
7531 2022-01-01         Valour Primary School    2B       33        2      2   
7532 2022-01-01     Northshore Primary School    2B       59        1      1   

     Balloting  Application Rate  
7352      SC<1          2.227273  
7353       NaN          0.000000  
7354      SC<1          2.400000  
7355       NaN          0.102564  
7356       NaN          0.000000  
...        ...               ...  
7528       NaN          0.032258  
7529       NaN          0.000000  
7530       NaN          0.025641  
7531       NaN          0.060606  
7532       NaN          0.016949  

[181 rows x 8 columns]

In [9]:
# Get indices of Phase 2C
df[(df['Year'] == '2022-01-01') & (df['Phase'] == '2C')]

Year                        School Phase  Vacancy  Applied  Taken  \
9863  2022-01-01      Admiralty Primary School    2C       45      104     45   
9864  2022-01-01  Ahmad Ibrahim Primary School    2C      129       31     31   
9865  2022-01-01                Ai Tong School    2C       42       86     42   
9866  2022-01-01      Alexandra Primary School    2C      113      146    113   
9867  2022-01-01   Anchor Green Primary School    2C      120       24     24   
...          ...                           ...   ...      ...      ...    ...   
10039 2022-01-01        Zhangde Primary School    2C       93       92     92   
10040 2022-01-01       Zhenghua Primary School    2C       90       68     68   
10041 2022-01-01       Zhonghua Primary School    2C      115        7      7   
10042 2022-01-01         Valour Primary School    2C       96      120     96   
10043 2022-01-01     Northshore Primary School    2C      175       75     75   

      Balloting  Application Rate  
9863       SC<1          2.311111  
9864        NaN          0.240310  
9865       SC<1          2.047619  
9866      SC<1#          1.292035  
9867        NaN          0.200000  
...         ...               ...  
10039       NaN          0.989247  
10040       NaN          0.755556  
10041       NaN          0.060870  
10042      SC<1          1.250000  
10043       NaN          0.428571  

[181 rows x 8 columns]

In [10]:
# Use MA3 for first model

forecast_df = pd.DataFrame()

for i in it.chain(range(2330, 2509), range(4841, 5020), range(7352, 7531), range(9863, 10042)):
    new_df = df[(df['School'] == df.iloc[i,1]) & (df['Phase'] == df.iloc[i,2])]
    new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
    new_df = new_df.reset_index()
    new_df=new_df.rename(columns={'Year':'ds', 'ApplicationRate_MA3':'y'})
    model = Prophet()
    model.fit(new_df);
    future = model.make_future_dataframe(periods=3, freq = 'y')
    forecast = model.predict(future)
    metric_df = forecast.set_index('ds')[['yhat']].join(new_df.set_index('ds').y).reset_index()
    metric_df.dropna(inplace=True)
    rsquared = r2_score(metric_df.y, metric_df.yhat)
    forecast['R-Squared'] = round(rsquared,4)
    forecast['School'] = df.iloc[i,1]
    forecast['Phase'] = df.iloc[i,2]
    forecast_df = pd.concat([forecast_df, forecast[['ds', 'School', 'Phase', 'yhat', 'yhat_lower', 'yhat_upper', 'R-Squared']]], ignore_index=True)

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:48:55 - cmdstanpy - INFO - Chain [1] start processing
22:48:55 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:48:55 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:07 - cmdstanpy - INFO - Chain [1] start processing
22:49:07 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:08 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:20 - cmdstanpy - INFO - Chain [1] start processing
22:49:20 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:21 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:32 - cmdstanpy - INFO - Chain [1] start processing
22:49:32 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:33 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:46 - cmdstanpy - INFO - Chain [1] start processing
22:49:46 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
22:49:47 - cmdstanp

...

23:07:05 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
23:07:06 - cmdstanpy - INFO - Chain [1] start processing
23:07:06 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['

23:07:19 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
23:07:20 - cmdstanpy - INFO - Chain [1] start processing
23:07:20 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['

23:07:34 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
23:07:35 - cmdstanpy - INFO - Chain [1] start processing
23:07:35 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['

23:07:47 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
23:07:48 - cmdstanpy - INFO - Chain [1] start processing
23:07:48 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['

23:07:59 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
23:08:00 - cmdstanpy - INFO - Chain [1] start processing
23:08:00 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2090921211.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['

In [11]:
# pd.set_option('display.max_rows', None)
forecast_df

ds                    School Phase      yhat  yhat_lower  \
0     2009-01-01  Admiralty Primary School     1  0.433710    0.401177   
1     2010-01-01  Admiralty Primary School     1  0.459706    0.425765   
2     2011-01-01  Admiralty Primary School     1  0.479880    0.447351   
3     2012-01-01  Admiralty Primary School     1  0.494215    0.461202   
4     2013-01-01  Admiralty Primary School     1  0.456796    0.422492   
...          ...                       ...   ...       ...         ...   
11919 2021-01-01   Zhonghua Primary School    2C  0.142386    0.064260   
11920 2022-01-01   Zhonghua Primary School    2C  0.102304    0.020544   
11921 2022-12-31   Zhonghua Primary School    2C  0.002810   -0.079445   
11922 2023-12-31   Zhonghua Primary School    2C -0.043418   -0.130737   
11923 2024-12-31   Zhonghua Primary School    2C -0.024283   -0.108717   

       yhat_upper  R-Squared  
0        0.468385     0.4593  
1        0.492743     0.4593  
2        0.510740     0.4593  
3        0.528525     0.4593  
4        0.490747     0.4593  
...           ...        ...  
11919    0.226584     0.6966  
11920    0.188687     0.6966  
11921    0.086103     0.6966  
11922    0.038299     0.6966  
11923    0.054648     0.6966  

[11924 rows x 7 columns]

In [12]:
exclude_df = forecast_df[(forecast_df['R-Squared'] > 0.7)]
exclude_df

ds                  School Phase      yhat  yhat_lower  \
34    2009-01-01          Ai Tong School     1  0.425600    0.409701   
35    2010-01-01          Ai Tong School     1  0.440250    0.423687   
36    2011-01-01          Ai Tong School     1  0.449502    0.432840   
37    2012-01-01          Ai Tong School     1  0.453353    0.436359   
38    2013-01-01          Ai Tong School     1  0.459226    0.443543   
...          ...                     ...   ...       ...         ...   
11885 2021-01-01  Zhangde Primary School    2C  0.945027    0.882364   
11886 2022-01-01  Zhangde Primary School    2C  0.922499    0.856530   
11887 2022-12-31  Zhangde Primary School    2C  0.819446    0.753294   
11888 2023-12-31  Zhangde Primary School    2C  0.752686    0.683052   
11889 2024-12-31  Zhangde Primary School    2C  0.810452    0.744522   

       yhat_upper  R-Squared  
34       0.442692     0.8354  
35       0.456505     0.8354  
36       0.466167     0.8354  
37       0.470161     0.8354  
38       0.475076     0.8354  
...           ...        ...  
11885    1.016332     0.7952  
11886    0.989274     0.7952  
11887    0.882053     0.7952  
11888    0.819836     0.7952  
11889    0.882630     0.7952  

[4788 rows x 7 columns]

In [13]:
new_df = pd.merge(df, exclude_df, how='outer', indicator=True)

In [14]:
second_df = new_df.loc[new_df._merge == 'left_only', ['Year', 'School', 'Phase', 'Vacancy', 'Applied', 'Taken', 'Balloting', 'Application Rate']]

In [15]:
second_df = second_df.sort_values(['Year', 'Phase'], ascending=True)
second_df.reset_index(inplace=True)
second_df.drop(['index'], axis=1, inplace=True)

In [38]:
second_df

Year                          School Phase  Vacancy  Applied  \
0    2009-01-01        Admiralty Primary School     1      300      168   
1    2009-01-01    Ahmad Ibrahim Primary School     1      180       57   
2    2009-01-01     Anchor Green Primary School     1      240       50   
3    2009-01-01       Ang Mo Kio Primary School     1      210       67   
4    2009-01-01  Anglo-Chinese School (Primary)     1      240       60   
...         ...                             ...   ...      ...      ...   
6133 2022-01-01        Palm View Primary School    2C      138       56   
6134 2022-01-01     Punggol View Primary School    2C       61       74   
6135 2022-01-01        Alexandra Primary School    2C      113      146   
6136 2022-01-01           Valour Primary School    2C       96      120   
6137 2022-01-01       Northshore Primary School    2C      175       75   

      Taken Balloting  Application Rate  
0       168       NaN          0.560000  
1        57       NaN          0.316667  
2        50       NaN          0.208333  
3        67       NaN          0.319048  
4        60       NaN          0.250000  
...     ...       ...               ...  
6133     56       NaN          0.405797  
6134     61      PR<1          1.213115  
6135    113     SC<1#          1.292035  
6136     96      SC<1          1.250000  
6137     75       NaN          0.428571  

[6138 rows x 8 columns]

In [16]:
second_df[(second_df['Year'] == '2022-01-01') & (second_df['Phase'] == '1')]

Year                          School Phase  Vacancy  Applied  \
5708 2022-01-01        Admiralty Primary School     1      150      107   
5709 2022-01-01    Ahmad Ibrahim Primary School     1      130       56   
5710 2022-01-01     Anchor Green Primary School     1      180       75   
5711 2022-01-01       Ang Mo Kio Primary School     1      150       48   
5712 2022-01-01  Anglo-Chinese School (Primary)     1      180       62   
...         ...                             ...   ...      ...      ...   
5810 2022-01-01        Palm View Primary School     1      180       93   
5811 2022-01-01   Sengkang Green Primary School     1      220      111   
5812 2022-01-01        Northoaks Primary School     1      160       29   
5813 2022-01-01           Valour Primary School     1      220      105   
5814 2022-01-01       Northshore Primary School     1      180       33   

      Taken Balloting  Application Rate  
5708    107       NaN          0.713333  
5709     56       NaN          0.430769  
5710     75       NaN          0.416667  
5711     48       NaN          0.320000  
5712     62       NaN          0.344444  
...     ...       ...               ...  
5810     93       NaN          0.516667  
5811    111       NaN          0.504545  
5812     29       NaN          0.181250  
5813    105       NaN          0.477273  
5814     33       NaN          0.183333  

[107 rows x 8 columns]

In [17]:
second_df[(second_df['Year'] == '2022-01-01') & (second_df['Phase'] == '2A')]

Year                        School Phase  Vacancy  Applied  Taken  \
5815 2022-01-01  Ahmad Ibrahim Primary School    2A       74        5      5   
5816 2022-01-01   Anchor Green Primary School    2A      105       46     46   
5817 2022-01-01       Anderson Primary School    2A       59       36     36   
5818 2022-01-01     Ang Mo Kio Primary School    2A      102       13     13   
5819 2022-01-01        Angsana Primary School    2A      162       20     20   
...         ...                           ...   ...      ...      ...    ...   
5889 2022-01-01        Zhangde Primary School    2A       45       11     11   
5890 2022-01-01       Zhonghua Primary School    2A       62        6      6   
5891 2022-01-01     Cantonment Primary School    2A       76        2      2   
5892 2022-01-01         Valour Primary School    2A      115       77     77   
5893 2022-01-01     Northshore Primary School    2A      147       31     31   

     Balloting  Application Rate  
5815       NaN          0.067568  
5816       NaN          0.438095  
5817       NaN          0.610169  
5818       NaN          0.127451  
5819       NaN          0.123457  
...        ...               ...  
5889       NaN          0.244444  
5890       NaN          0.096774  
5891       NaN          0.026316  
5892       NaN          0.669565  
5893       NaN          0.210884  

[79 rows x 8 columns]

In [18]:
second_df[(second_df['Year'] == '2022-01-01') & (second_df['Phase'] == '2B')]

Year                       School Phase  Vacancy  Applied  Taken  \
5894 2022-01-01     Admiralty Primary School    2B       22       49     22   
5895 2022-01-01               Ai Tong School    2B       20       48     20   
5896 2022-01-01  Anchor Green Primary School    2B       40        0      0   
5897 2022-01-01      Anderson Primary School    2B       28       21     21   
5898 2022-01-01    Ang Mo Kio Primary School    2B       50        0      0   
...         ...                          ...   ...      ...      ...    ...   
6027 2022-01-01  Punggol View Primary School    2B       20        0      0   
6028 2022-01-01     Riverside Primary School    2B       20        2      2   
6029 2022-01-01    Springdale Primary School    2B       29        0      0   
6030 2022-01-01        Valour Primary School    2B       33        2      2   
6031 2022-01-01    Northshore Primary School    2B       59        1      1   

     Balloting  Application Rate  
5894      SC<1          2.227273  
5895      SC<1          2.400000  
5896       NaN          0.000000  
5897       NaN          0.750000  
5898       NaN          0.000000  
...        ...               ...  
6027       NaN          0.000000  
6028       NaN          0.100000  
6029       NaN          0.000000  
6030       NaN          0.060606  
6031       NaN          0.016949  

[138 rows x 8 columns]

In [19]:
second_df[(second_df['Year'] == '2022-01-01') & (second_df['Phase'] == '2C')]

Year                          School Phase  Vacancy  Applied  \
6032 2022-01-01        Admiralty Primary School    2C       45      104   
6033 2022-01-01                  Ai Tong School    2C       42       86   
6034 2022-01-01     Anchor Green Primary School    2C      120       24   
6035 2022-01-01         Anderson Primary School    2C       64       88   
6036 2022-01-01  Anglo-Chinese School (Primary)    2C       55       69   
...         ...                             ...   ...      ...      ...   
6133 2022-01-01        Palm View Primary School    2C      138       56   
6134 2022-01-01     Punggol View Primary School    2C       61       74   
6135 2022-01-01        Alexandra Primary School    2C      113      146   
6136 2022-01-01           Valour Primary School    2C       96      120   
6137 2022-01-01       Northshore Primary School    2C      175       75   

      Taken Balloting  Application Rate  
6032     45      SC<1          2.311111  
6033     42      SC<1          2.047619  
6034     24       NaN          0.200000  
6035     64     SC1-2          1.375000  
6036     55      SC<1          1.254545  
...     ...       ...               ...  
6133     56       NaN          0.405797  
6134     61      PR<1          1.213115  
6135    113     SC<1#          1.292035  
6136     96      SC<1          1.250000  
6137     75       NaN          0.428571  

[106 rows x 8 columns]

In [62]:
# Use MA3 and changepoint_prior_scale=0.3 for second model

forecast_df2 = pd.DataFrame()

for i in it.chain(range(5708, 5814), range(5815, 5892), range(5894, 6030), range(6032, 6136)):
    new_df = second_df[(second_df['School'] == second_df.iloc[i,1]) & (second_df['Phase'] == second_df.iloc[i,2])]
    new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
    new_df = new_df.reset_index()
    new_df=new_df.rename(columns={'Year':'ds', 'ApplicationRate_MA3':'y'})
    model = Prophet(changepoint_prior_scale=0.3)
    model.fit(new_df);
    future = model.make_future_dataframe(periods=3, freq = 'y')
    forecast = model.predict(future)
    metric_df = forecast.set_index('ds')[['yhat']].join(new_df.set_index('ds').y).reset_index()
    metric_df.dropna(inplace=True)
    rsquared = r2_score(metric_df.y, metric_df.yhat)
    forecast['R-Squared'] = round(rsquared,4)
    forecast['School'] = second_df.iloc[i,1]
    forecast['Phase'] = second_df.iloc[i,2]
    forecast_df2 = pd.concat([forecast_df2, forecast[['ds', 'School', 'Phase', 'yhat', 'yhat_lower', 'yhat_upper', 'R-Squared']]], ignore_index=True)    

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:23:02 - cmdstanpy - INFO - Chain [1] start processing
10:23:02 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:23:03 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:23:35 - cmdstanpy - INFO - Chain [1] start processing
10:23:42 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:23:42 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:24:57 - cmdstanpy - INFO - Chain [1] start processing
10:25:04 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:25:04 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:25:51 - cmdstanpy - INFO - Chain [1] start processing
10:25:51 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:25:52 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:26:57 - cmdstanpy - INFO - Chain [1] start processing
10:26:57 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:26:58 - cmdstanp

...

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:36:19 - cmdstanpy - INFO - Chain [1] start processing
10:36:19 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:36:20 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:36:58 - cmdstanpy - INFO - Chain [1] start processing
10:36:58 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:36:59 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:37:29 - cmdstanpy - INFO - Chain [1] start processing
10:37:29 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:37:30 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:38:13 - cmdstanpy - INFO - Chain [1] start processing
10:38:19 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:38:20 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:39:10 - cmdstanpy - INFO - Chain [1] start processing
10:39:16 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/2669438502.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA3'] = new_df['Application Rate'].rolling(3).mean()
10:39:17 - cmdstanp

In [63]:
forecast_df2

ds                    School Phase      yhat  yhat_lower  \
0    2009-01-01  Admiralty Primary School     1  0.537200    0.523929   
1    2010-01-01  Admiralty Primary School     1  0.538921    0.525549   
2    2011-01-01  Admiralty Primary School     1  0.529005    0.516222   
3    2012-01-01  Admiralty Primary School     1  0.507434    0.494627   
4    2013-01-01  Admiralty Primary School     1  0.452226    0.439414   
...         ...                       ...   ...       ...         ...   
7138 2021-01-01  Alexandra Primary School    2C  1.351393    1.351393   
7139 2022-01-01  Alexandra Primary School    2C  1.371068    1.371068   
7140 2022-12-31  Alexandra Primary School    2C  1.468662    1.432870   
7141 2023-12-31  Alexandra Primary School    2C  1.533164    1.401127   
7142 2024-12-31  Alexandra Primary School    2C  1.476085    1.213754   

      yhat_upper  R-Squared  
0       0.549918     0.9161  
1       0.552025     0.9161  
2       0.541484     0.9161  
3       0.520376     0.9161  
4       0.466200     0.9161  
...          ...        ...  
7138    1.351393     1.0000  
7139    1.371068     1.0000  
7140    1.502791     1.0000  
7141    1.651856     1.0000  
7142    1.705046     1.0000  

[7143 rows x 7 columns]

In [64]:
exclude_df2 = forecast_df2[(forecast_df2['R-Squared'] > 0.7)]
exclude_df2

ds                    School Phase      yhat  yhat_lower  \
0    2009-01-01  Admiralty Primary School     1  0.537200    0.523929   
1    2010-01-01  Admiralty Primary School     1  0.538921    0.525549   
2    2011-01-01  Admiralty Primary School     1  0.529005    0.516222   
3    2012-01-01  Admiralty Primary School     1  0.507434    0.494627   
4    2013-01-01  Admiralty Primary School     1  0.452226    0.439414   
...         ...                       ...   ...       ...         ...   
7138 2021-01-01  Alexandra Primary School    2C  1.351393    1.351393   
7139 2022-01-01  Alexandra Primary School    2C  1.371068    1.371068   
7140 2022-12-31  Alexandra Primary School    2C  1.468662    1.432870   
7141 2023-12-31  Alexandra Primary School    2C  1.533164    1.401127   
7142 2024-12-31  Alexandra Primary School    2C  1.476085    1.213754   

      yhat_upper  R-Squared  
0       0.549918     0.9161  
1       0.552025     0.9161  
2       0.541484     0.9161  
3       0.520376     0.9161  
4       0.466200     0.9161  
...          ...        ...  
7138    1.351393     1.0000  
7139    1.371068     1.0000  
7140    1.502791     1.0000  
7141    1.651856     1.0000  
7142    1.705046     1.0000  

[4369 rows x 7 columns]

In [65]:
new_df2 = pd.merge(second_df, exclude_df2, how='outer', indicator=True)

In [66]:
third_df = new_df2.loc[new_df2._merge == 'left_only', ['Year', 'School', 'Phase', 'Vacancy', 'Applied', 'Taken', 'Balloting', 'Application Rate']]

In [67]:
third_df = third_df.sort_values(['Year', 'Phase'], ascending=True)
third_df.reset_index(inplace=True)
third_df.drop(['index'], axis=1, inplace=True)

In [68]:
third_df

Year                        School Phase  Vacancy  Applied  Taken  \
0    2009-01-01   Anchor Green Primary School     1      240       50     50   
1    2009-01-01  Bukit Panjang Primary School     1      240      142    142   
2    2009-01-01    Bukit Timah Primary School     1      180       46     46   
3    2009-01-01          Eunos Primary School     1      180       61     61   
4    2009-01-01         Fuchun Primary School     1      270      131    131   
...         ...                           ...   ...      ...      ...    ...   
2541 2022-01-01  St. Gabriel's Primary School    2C       77       77     77   
2542 2022-01-01      Yangzheng Primary School    2C       58      101     58   
2543 2022-01-01          Yumin Primary School    2C      109       20     20   
2544 2022-01-01         Valour Primary School    2C       96      120     96   
2545 2022-01-01     Northshore Primary School    2C      175       75     75   

     Balloting  Application Rate  
0          NaN          0.208333  
1          NaN          0.591667  
2          NaN          0.255556  
3          NaN          0.338889  
4          NaN          0.485185  
...        ...               ...  
2541       NaN          1.000000  
2542      SC<1          1.741379  
2543       NaN          0.183486  
2544      SC<1          1.250000  
2545       NaN          0.428571  

[2546 rows x 8 columns]

In [69]:
third_df[(third_df['Year'] == '2022-01-01')]

Year                              School Phase  Vacancy  Applied  \
2375 2022-01-01         Anchor Green Primary School     1      180       75   
2376 2022-01-01        Bukit Panjang Primary School     1      180      100   
2377 2022-01-01          Bukit Timah Primary School     1      130       59   
2378 2022-01-01               Fuchun Primary School     1      150       51   
2379 2022-01-01  Geylang Methodist School (Primary)     1      210      103   
...         ...                                 ...   ...      ...      ...   
2541 2022-01-01        St. Gabriel's Primary School    2C       77       77   
2542 2022-01-01            Yangzheng Primary School    2C       58      101   
2543 2022-01-01                Yumin Primary School    2C      109       20   
2544 2022-01-01               Valour Primary School    2C       96      120   
2545 2022-01-01           Northshore Primary School    2C      175       75   

      Taken Balloting  Application Rate  
2375     75       NaN          0.416667  
2376    100       NaN          0.555556  
2377     59       NaN          0.453846  
2378     51       NaN          0.340000  
2379    103       NaN          0.490476  
...     ...       ...               ...  
2541     77       NaN          1.000000  
2542     58      SC<1          1.741379  
2543     20       NaN          0.183486  
2544     96      SC<1          1.250000  
2545     75       NaN          0.428571  

[171 rows x 8 columns]

In [71]:
# Use MA2 and changepoint_prior_scale=0.6 for third model

forecast_df3 = pd.DataFrame()

for i in range(2375, 2546):
    new_df = third_df[(third_df['School'] == third_df.iloc[i,1]) & (third_df['Phase'] == third_df.iloc[i,2])]
    new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
    new_df = new_df.reset_index()
    new_df=new_df.rename(columns={'Year':'ds', 'ApplicationRate_MA2':'y'})
    model = Prophet(changepoint_prior_scale=0.6)
    model.fit(new_df);
    future = model.make_future_dataframe(periods=3, freq = 'y')
    forecast = model.predict(future)
    metric_df = forecast.set_index('ds')[['yhat']].join(new_df.set_index('ds').y).reset_index()
    metric_df.dropna(inplace=True)
    rsquared = r2_score(metric_df.y, metric_df.yhat)
    forecast['R-Squared'] = round(rsquared,4)
    forecast['School'] = third_df.iloc[i,1]
    forecast['Phase'] = third_df.iloc[i,2]
    forecast_df3 = pd.concat([forecast_df3, forecast[['ds', 'School', 'Phase', 'yhat', 'yhat_lower', 'yhat_upper', 'R-Squared']]], ignore_index=True)    

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:43:43 - cmdstanpy - INFO - Chain [1] start processing
10:43:43 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:43:44 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:44:32 - cmdstanpy - INFO - Chain [1] start processing
10:44:32 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:44:32 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:44:51 - cmdstanpy - INFO - Chain [1] start processing
10:44:51 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:44:52 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:45:08 - cmdstanpy - INFO - Chain [1] start processing
10:45:09 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:45:09 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:45:21 - cmdstanpy - INFO - Chain [1] start processing
10:45:21 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:45:22 - cmdstanp

...

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:46:23 - cmdstanpy - INFO - Chain [1] start processing
10:46:23 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:46:24 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:46:41 - cmdstanpy - INFO - Chain [1] start processing
10:46:41 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:46:42 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:47:12 - cmdstanpy - INFO - Chain [1] start processing
10:47:12 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:47:13 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:47:45 - cmdstanpy - INFO - Chain [1] start processing
10:47:46 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:47:46 - cmdstanp

C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:48:21 - cmdstanpy - INFO - Chain [1] start processing
10:48:21 - cmdstanpy - INFO - Chain [1] done processing
C:\Users\wujin\AppData\Local\Temp/ipykernel_38496/3220654538.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['ApplicationRate_MA2'] = new_df['Application Rate'].rolling(2).mean()
10:48:21 - cmdstanp

In [72]:
exclude_df3 = forecast_df3[(forecast_df3['R-Squared'] < 0.7)]
exclude_df3

ds                    School Phase      yhat  yhat_lower  \
51   2009-01-01     Fuchun Primary School     1  0.524542    0.474684   
52   2010-01-01     Fuchun Primary School     1  0.487377    0.438444   
53   2011-01-01     Fuchun Primary School     1  0.460207    0.413954   
54   2012-01-01     Fuchun Primary School     1  0.443058    0.393499   
55   2013-01-01     Fuchun Primary School     1  0.502897    0.452487   
...         ...                       ...   ...       ...         ...   
2784 2021-01-01  Yangzheng Primary School    2C  1.519231    1.249974   
2785 2022-01-01  Yangzheng Primary School    2C  1.555724    1.266910   
2786 2022-12-31  Yangzheng Primary School    2C  1.307892    1.035611   
2787 2023-12-31  Yangzheng Primary School    2C  1.225740    0.948930   
2788 2024-12-31  Yangzheng Primary School    2C  1.545685    1.279452   

      yhat_upper  R-Squared  
51      0.572813     0.5760  
52      0.531162     0.5760  
53      0.506107     0.5760  
54      0.491733     0.5760  
55      0.550143     0.5760  
...          ...        ...  
2784    1.784578     0.3757  
2785    1.804020     0.3757  
2786    1.593020     0.3757  
2787    1.482586     0.3757  
2788    1.816365     0.3757  

[1627 rows x 7 columns]

In [73]:
# Get number of rows which has R-squared < 0.7
exclude_df3[(exclude_df3['ds'] == '2022-01-01')]

ds                                   School Phase      yhat  \
64   2022-01-01                    Fuchun Primary School     1  0.409211   
81   2022-01-01       Geylang Methodist School (Primary)     1  0.411147   
115  2022-01-01                   Lianhua Primary School     1  0.246924   
149  2022-01-01                  Meridian Primary School     1  0.243498   
166  2022-01-01                 Northland Primary School     1  0.556050   
...         ...                                      ...   ...       ...   
2649 2022-01-01                 Marymount Convent School    2C  0.458021   
2717 2022-01-01                            Rosyth School    2C  4.430452   
2751 2022-01-01  Singapore Chinese Girls' Primary School    2C  1.785879   
2768 2022-01-01             St. Gabriel's Primary School    2C  0.988498   
2785 2022-01-01                 Yangzheng Primary School    2C  1.555724   

      yhat_lower  yhat_upper  R-Squared  
64      0.359628    0.457625     0.5760  
81      0.394121    0.429649     0.4725  
115     0.188621    0.301331     0.2939  
149     0.157379    0.334096     0.2792  
166     0.502550    0.606589     0.4872  
...          ...         ...        ...  
2649    0.339521    0.588032     0.5259  
2717    3.650561    5.211829     0.4286  
2751    1.581380    1.981171     0.6790  
2768    0.803062    1.162683     0.3548  
2785    1.266910    1.804020     0.3757  

[96 rows x 7 columns]

In [74]:
len(df[df['Year'] == '2022-01-01'])

724

In [75]:
# 87% of the predictions have R-Squared of more than 0.7
len(exclude_df3[(exclude_df3['ds'] == '2022-01-01')])/len(df[df['Year'] == '2022-01-01'])

0.13259668508287292

In [76]:
pdlist = [exclude_df, exclude_df2, forecast_df3]
predictions_df = pd.concat(pdlist)

In [77]:
predictions_df

ds                     School Phase      yhat  yhat_lower  \
34   2009-01-01             Ai Tong School     1  0.425600    0.409701   
35   2010-01-01             Ai Tong School     1  0.440250    0.423687   
36   2011-01-01             Ai Tong School     1  0.449502    0.432840   
37   2012-01-01             Ai Tong School     1  0.453353    0.436359   
38   2013-01-01             Ai Tong School     1  0.459226    0.443543   
...         ...                        ...   ...       ...         ...   
2814 2021-01-01  Northshore Primary School    2C  0.311475    0.311475   
2815 2022-01-01  Northshore Primary School    2C  0.413857    0.413857   
2816 2022-12-31  Northshore Primary School    2C  0.515957    0.515957   
2817 2023-12-31  Northshore Primary School    2C  0.618338    0.618338   
2818 2024-12-31  Northshore Primary School    2C  0.721000    0.721000   

      yhat_upper  R-Squared  
34      0.442692     0.8354  
35      0.456505     0.8354  
36      0.466167     0.8354  
37      0.470161     0.8354  
38      0.475076     0.8354  
...          ...        ...  
2814    0.311475     1.0000  
2815    0.413857     1.0000  
2816    0.515957     1.0000  
2817    0.618338     1.0000  
2818    0.721000     1.0000  

[11976 rows x 7 columns]

In [142]:
preds = predictions_df[(predictions_df['ds'] == '2022-01-01')]

len(preds)

724

In [89]:
predictions_3_years = predictions_df[(predictions_df['ds'] > '2022-01-01')]

In [92]:
predictions_3_years.rename(columns={'ds': 'Year', 'yhat': 'Application Rate'}, inplace=True)

C:\Users\wujin\anaconda3\lib\site-packages\pandas\core\frame.py:5039: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


In [131]:
predictions_3_years

Year                                        School Phase  \
48    2022-12-31                                Ai Tong School     1   
49    2023-12-31                                Ai Tong School     1   
50    2024-12-31                                Ai Tong School     1   
61    2022-12-31                      Alexandra Primary School     1   
62    2023-12-31                      Alexandra Primary School     1   
63    2024-12-31                      Alexandra Primary School     1   
95    2022-12-31                       Anderson Primary School     1   
96    2023-12-31                       Anderson Primary School     1   
97    2024-12-31                       Anderson Primary School     1   
129   2022-12-31                 Anglo-Chinese School (Junior)     1   
130   2023-12-31                 Anglo-Chinese School (Junior)     1   
131   2024-12-31                 Anglo-Chinese School (Junior)     1   
214   2022-12-31                      Bendemeer Primary School     1   
215   2023-12-31                      Bendemeer Primary School     1   
216   2024-12-31                      Bendemeer Primary School     1   
366   2022-12-31                      Casuarina Primary School     1   
367   2023-12-31                      Casuarina Primary School     1   
368   2024-12-31                      Casuarina Primary School     1   
383   2022-12-31                Catholic High School (Primary)     1   
384   2023-12-31                Catholic High School (Primary)     1   
385   2024-12-31                Catholic High School (Primary)     1   
519   2022-12-31                      CHIJ Primary (Toa Payoh)     1   
520   2023-12-31                      CHIJ Primary (Toa Payoh)     1   
521   2024-12-31                      CHIJ Primary (Toa Payoh)     1   
536   2022-12-31               CHIJ St. Nicholas Girls' School     1   
537   2023-12-31               CHIJ St. Nicholas Girls' School     1   
538   2024-12-31               CHIJ St. Nicholas Girls' School     1   
553   2022-12-31                                Chongfu School     1   
554   2023-12-31                                Chongfu School     1   
555   2024-12-31                                Chongfu School     1   
570   2022-12-31                     Chongzheng Primary School     1   
571   2023-12-31                     Chongzheng Primary School     1   
572   2024-12-31                     Chongzheng Primary School     1   
689   2022-12-31                        Dazhong Primary School     1   
690   2023-12-31                        Dazhong Primary School     1   
691   2024-12-31                        Dazhong Primary School     1   
706   2022-12-31                            De La Salle School     1   
707   2023-12-31                            De La Salle School     1   
708   2024-12-31                            De La Salle School     1   
723   2022-12-31                    East Spring Primary School     1   
724   2023-12-31                    East Spring Primary School     1   
725   2024-12-31                    East Spring Primary School     1   
757   2022-12-31                     Elias Park Primary School     1   
758   2023-12-31                     Elias Park Primary School     1   
759   2024-12-31                     Elias Park Primary School     1   
791   2022-12-31                      Evergreen Primary School     1   
792   2023-12-31                      Evergreen Primary School     1   
793   2024-12-31                      Evergreen Primary School     1   
825   2022-12-31                    Farrer Park Primary School     1   
826   2023-12-31                    Farrer Park Primary School     1   
827   2024-12-31                    Farrer Park Primary School     1   
851   2022-12-31                     Fern Green Primary School     1   
852   2023-12-31                     Fern Green Primary School     1   
853   2024-12-31                     Fern Green Primary School     1   
868   2022-12-31                       Fernvale Prim

In [132]:
combined_df = pd.merge(df, predictions_3_years, how='outer', indicator=True)

In [133]:
# new_combined_df = combined_df.loc[combined_df._merge == 'right_only', ['Year', 'School', 'Phase','Application Rate']]
combined_prediction = combined_df[['Year', 'School', 'Phase','Application Rate']]

In [134]:
combined_prediction = combined_prediction.sort_values(['School', 'Phase'], ascending=True)
combined_prediction.reset_index(inplace=True)
combined_prediction.drop(['index'], axis=1, inplace=True)
df_1.loc[df_1['B']<0,'B']=0

In [143]:
combined_prediction.loc[combined_prediction['Application Rate']<0, 'Application Rate'] = 0.0001

In [144]:
combined_prediction

Year                                        School Phase  \
0     2009-01-01                      Admiralty Primary School     1   
1     2010-01-01                      Admiralty Primary School     1   
2     2011-01-01                      Admiralty Primary School     1   
3     2012-01-01                      Admiralty Primary School     1   
4     2013-01-01                      Admiralty Primary School     1   
5     2014-01-01                      Admiralty Primary School     1   
6     2015-01-01                      Admiralty Primary School     1   
7     2016-01-01                      Admiralty Primary School     1   
8     2017-01-01                      Admiralty Primary School     1   
9     2018-01-01                      Admiralty Primary School     1   
10    2019-01-01                      Admiralty Primary School     1   
11    2020-01-01                      Admiralty Primary School     1   
12    2021-01-01                      Admiralty Primary School     1   
13    2022-01-01                      Admiralty Primary School     1   
14    2022-12-31                      Admiralty Primary School     1   
15    2023-12-31                      Admiralty Primary School     1   
16    2024-12-31                      Admiralty Primary School     1   
17    2009-01-01                      Admiralty Primary School    2A   
18    2010-01-01                      Admiralty Primary School    2A   
19    2011-01-01                      Admiralty Primary School    2A   
20    2012-01-01                      Admiralty Primary School    2A   
21    2013-01-01                      Admiralty Primary School    2A   
22    2014-01-01                      Admiralty Primary School    2A   
23    2015-01-01                      Admiralty Primary School    2A   
24    2016-01-01                      Admiralty Primary School    2A   
25    2017-01-01                      Admiralty Primary School    2A   
26    2018-01-01                      Admiralty Primary School    2A   
27    2019-01-01                      Admiralty Primary School    2A   
28    2020-01-01                      Admiralty Primary School    2A   
29    2021-01-01                      Admiralty Primary School    2A   
30    2022-01-01                      Admiralty Primary School    2A   
31    2022-12-31                      Admiralty Primary School    2A   
32    2023-12-31                      Admiralty Primary School    2A   
33    2024-12-31                      Admiralty Primary School    2A   
34    2009-01-01                      Admiralty Primary School    2B   
35    2010-01-01                      Admiralty Primary School    2B   
36    2011-01-01                      Admiralty Primary School    2B   
37    2012-01-01                      Admiralty Primary School    2B   
38    2013-01-01                      Admiralty Primary School    2B   
39    2014-01-01                      Admiralty Primary School    2B   
40    2015-01-01                      Admiralty Primary School    2B   
41    2016-01-01                      Admiralty Primary School    2B   
42    2017-01-01                      Admiralty Primary School    2B   
43    2018-01-01                      Admiralty Primary School    2B   
44    2019-01-01                      Admiralty Primary School    2B   
45    2020-01-01                      Admiralty Primary School    2B   
46    2021-01-01                      Admiralty Primary School    2B   
47    2022-01-01                      Admiralty Primary School    2B   
48    2022-12-31                      Admiralty Primary School    2B   
49    2023-12-31                      Admiralty Primary School    2B   
50    2024-12-31                      Admiralty Primary School    2B   
51    2009-01-01                      Admiralty Primary School    2C   
52    2010-01-01                      Admiralty Primary School    2C   
53    2011-01-01                      Admiralty Primary School    2C   
54    2012-01-01                      Admiralty Prim

In [145]:
combined_prediction.to_csv('combined_prediction.csv')